In [1]:
#  Dependencies

from pickle import APPEND
from pprint import PrettyPrinter
from urllib import request
from flask import Flask
import requests
from pprint import pprint
import pandas as pd
import matplotlib
# from flask import render_template
# from flask_sqlalchemy import SQLAlchemy

# SQLAlchemy
from sqlalchemy import create_engine



In [2]:
# Chart 1 - Scatter Plot - Velocity vs Magnitude
# API request

# 50 years range
# append velmag to data_1 before it's turned into a df
# drop the NoneType data row

basic_url_1 = 'https://ssd-api.jpl.nasa.gov/cad.api?date-min=2022-01-01&date-max=2072-01-01&body=ALL' #5516 results

response1 = requests.get(basic_url_1)
data_1 = response1.json()

# is now returning 5516

In [32]:
pprint(data_1)

{'count': '10487',
 'data': [['2022 AJ1',
           '2',
           '2459580.642421097',
           '2022-Jan-01 03:25',
           '0.00524130200804947',
           '0.00520274467068745',
           '0.00527991800632925',
           '11.9842220841328',
           '11.9837003140226',
           '00:02',
           'Moon',
           '27.86'],
          ['2022 AJ1',
           '2',
           '2459580.875887923',
           '2022-Jan-01 09:01',
           '0.00515067131037624',
           '0.00510945511471365',
           '0.00519188216996143',
           '11.1602139720087',
           '11.1137645065506',
           '< 00:01',
           'Earth',
           '27.86'],
          ['2021 BD',
           '3',
           '2459580.918171884',
           '2022-Jan-01 10:02',
           '0.0393055681764869',
           '0.0261976472427462',
           '0.0539959353006968',
           '45.8448630366018',
           '45.8447813065924',
           '12:05',
           'Mercury',
           '26.9'],

In [20]:
index_name = data_1['fields']
index_name

['des',
 'orbit_id',
 'jd',
 'cd',
 'dist',
 'dist_min',
 'dist_max',
 'v_rel',
 'v_inf',
 't_sigma_f',
 'body',
 'h']

In [3]:
# Chart 1
# Data collection

# Clean data_1 for objects that have a NoneType
# for x in data_1['data']:
#     if x[10] == None:
#         data_1.pop(x)
                                                                          
# # # the obj once we find it.                                                      
# for x in range(len(data_1)):
#     if data_1['data'][x][10] == None:
#         data_1.pop(x)


# print(len(data_1.values()))
# pprint(data_1)

# List for velocity ('v-rel') - X-axis 
v_rel = []
for x in data_1['data']:
    v_rel.append(x[7])

print(len(v_rel))        # 10487 results

# List for magnitude ('h') - Y-axis
h = []
for x in data_1['data']:
    if x[11] == None:
        h.append(0)
    else:
        h.append(x[11])
print(len(h))           # 10487 results
# workaround for one None value. Magnitude being none doesn't make physical sense though
# * 0

# print(len(mag))        # 5515 results

#vel, mag and velMag no longer nec as seperate lists

10511
10511


In [32]:
data_1.keys()

dict_keys(['signature', 'count', 'fields', 'data'])

In [4]:
from dis import dis


des = []
orbit_id=[]
jd=[]
cd=[]
dist=[]
dist_min=[]
dist_max=[]
v_rel=[]
v_inf = []
t_sigma_f=[]
body = []
h = []
obj_id = []
for i in range(len(data_1['data'])):
    des.append(data_1['data'][i][0])
    orbit_id.append(data_1['data'][i][1])
    jd.append(data_1['data'][i][2])
    cd.append(data_1['data'][i][3])
    dist.append(data_1['data'][i][4])
    dist_min.append(data_1['data'][i][5])
    dist_max.append(data_1['data'][i][6])
    v_rel.append(data_1['data'][i][7])
    v_inf.append(data_1['data'][i][8])
    t_sigma_f.append(data_1['data'][i][9])
    body.append(data_1['data'][i][10])
    h.append(data_1['data'][i][11])
    obj_id.append(i)
    
    
    


In [5]:
# Make df, create lists to add, include mag*vel
NEO_df = pd.DataFrame ({
                        'id': obj_id,
                        'des': des,
                        'orbit_id' : orbit_id,
                        'jd': jd,
                        # 'cd': cd,
                        'dist': dist,
                        'dist_min': dist_min,
                        'dist_max': dist_max,
                        'v_inf': v_inf,
                        "v_rel":v_rel,
                        't_sigma_f':t_sigma_f,
                        "body": body,
                        'h' : h
                        
                        })
NEO_df.head()
# not sure if i can make the df with the dict structure of the json

id        des orbit_id                 jd                 dist  \
0   0   2022 AJ1        2  2459580.642421097  0.00524130200804947   
1   1   2022 AJ1        2  2459580.875887923  0.00515067131037624   
2   2    2021 BD        3  2459580.918171884   0.0393055681764869   
3   3  2013 GV68       42  2459581.338275973   0.0458370379931804   
4   4   2022 AM3        2  2459581.485058938   0.0266412770857508   

              dist_min             dist_max             v_inf  \
0  0.00520274467068745  0.00527991800632925  11.9837003140226   
1  0.00510945511471365  0.00519188216996143  11.1137645065506   
2   0.0261976472427462   0.0539959353006968  45.8447813065924   
3   0.0458346666479921   0.0458394098937773  28.1881689352989   
4   0.0264882041954083   0.0267943446676206  6.86988748883059   

              v_rel t_sigma_f     body      h  
0  11.9842220841328     00:02     Moon  27.86  
1  11.1602139720087   < 00:01    Earth  27.86  
2  45.8448630366018     12:05  Mercury   26.9  
3  28.1882829187049   < 00:01  Mercury  19.02  
4  6.88443029643995     00:01    Earth  26.57

In [25]:
NEO_df['cd']= pd.to_datetime(NEO_df['cd'])

KeyError: 'cd'

In [6]:
NEO_df.head()

id        des orbit_id                 jd                 dist  \
0   0   2022 AJ1        2  2459580.642421097  0.00524130200804947   
1   1   2022 AJ1        2  2459580.875887923  0.00515067131037624   
2   2    2021 BD        3  2459580.918171884   0.0393055681764869   
3   3  2013 GV68       42  2459581.338275973   0.0458370379931804   
4   4   2022 AM3        2  2459581.485058938   0.0266412770857508   

              dist_min             dist_max             v_inf  \
0  0.00520274467068745  0.00527991800632925  11.9837003140226   
1  0.00510945511471365  0.00519188216996143  11.1137645065506   
2   0.0261976472427462   0.0539959353006968  45.8447813065924   
3   0.0458346666479921   0.0458394098937773  28.1881689352989   
4   0.0264882041954083   0.0267943446676206  6.86988748883059   

              v_rel t_sigma_f     body      h  
0  11.9842220841328     00:02     Moon  27.86  
1  11.1602139720087   < 00:01    Earth  27.86  
2  45.8448630366018     12:05  Mercury   26.9  
3  28.1882829187049   < 00:01  Mercury  19.02  
4  6.88443029643995     00:01    Earth  26.57

In [ ]:
# ******* data base ********

In [38]:
from sqlalchemy import create_engine
from sqlalchemy.orm import sessionmaker
from sqlalchemy import Table, Column, Integer, Numeric, String
from sqlalchemy.ext.declarative import declarative_base
Base = declarative_base()
import pandas as pd
import sqlite3 

In [20]:
conn = sqlite3.connect('NEO.db')

In [21]:
from datetime import date, datetime
import string


class NEO(Base):
    __tablename__ = 'NEOs'
    id = Column(Numeric(),primary_key = True, index = True)
    des = Column(String(225))
    orbit_id = Column(Integer())
    jd = Column(String(40))
    # cd = Column(datetime(2073,12,30,23,59,59))
    dist = Column(String())
    dist_min = Column(String())
    dist_max = Column(String())
    v_rel = Column(Numeric())
    v_inf = Column(Numeric())
    t_sigma_f = Column(String(40))
    body = Column(String(20))
    h = Column(Numeric())


In [39]:
path = 'NEO.db'                                     
engine = create_engine(f'sqlite:///{path}')



In [23]:
Base.metadata.create_all(engine)

In [24]:
from sqlalchemy.orm import Session
session = Session(bind=engine)

In [25]:
for index, row in NEO_df.iterrows():
    data_all = NEO(id=row['id'],des = row['des'],orbit_id=row['orbit_id'], jd=row['jd'],dist=row['dist'],dist_min=row['dist_min'],dist_max=row['dist_max'],v_rel=row['v_rel'],v_inf=row['v_inf'],t_sigma_f=row['t_sigma_f'],body=row['body'],h=row['h'])
    session.add(data_all)
    session.commit()    

In [26]:
data = pd.read_sql('select * from NEOs',engine)        
data.head() 

id        des orbit_id                 jd                 dist  \
0   0   2022 AJ1        2  2459580.642421097  0.00524130200804947   
1   1   2022 AJ1        2  2459580.875887923  0.00515067131037624   
2   2    2021 BD        3  2459580.918171884   0.0393055681764869   
3   3  2013 GV68       42  2459581.338275973   0.0458370379931804   
4   4   2022 AM3        2  2459581.485058938   0.0266412770857508   

              dist_min             dist_max      v_rel      v_inf t_sigma_f  \
0  0.00520274467068745  0.00527991800632925  11.984222  11.983700     00:02   
1  0.00510945511471365  0.00519188216996143  11.160214  11.113765   < 00:01   
2   0.0261976472427462   0.0539959353006968  45.844863  45.844781     12:05   
3   0.0458346666479921   0.0458394098937773  28.188283  28.188169   < 00:01   
4   0.0264882041954083   0.0267943446676206   6.884430   6.869887     00:01   

      body      h  
0     Moon  27.86  
1    Earth  27.86  
2  Mercury  26.90  
3  Mercury  19.02  
4    Earth  26.57

In [40]:
query = session.query(NEO).filter_by(body='Moon')
for result in query:
    print(result.h)

27.8600000000
28.3600000000
29.1300000000
27.3500000000
29.6000000000
31.8200000000
28.4700000000
29.7000000000
28.1800000000
27.6600000000
25.8700000000
29.2000000000
26.8000000000
30.1400000000
29.0800000000
26.7900000000
27.5600000000
25.2600000000
27.3900000000
26.9500000000
26.3000000000
28.1100000000
28.4700000000
29.5100000000
29.9300000000
29.8200000000
27.4800000000
27.0500000000
30.8600000000
27.3200000000
27.1200000000
29.3200000000
27.1500000000
25.2200000000
26.3300000000
27.8400000000
26.4400000000
27.2100000000
29.7600000000
25.0600000000
27.9500000000
25.8000000000
25.5200000000
27.2500000000
26.1900000000
28.0800000000
29.1200000000
27.9800000000
29.3300000000
28.1300000000
30.5300000000
26.2100000000
28.6000000000
26.9200000000
26.5800000000
27.1600000000
27.3500000000
30.3000000000
27.7100000000
28.6300000000
28.0000000000
29.6600000000
26.0500000000
27.3500000000
25.8200000000
25.7900000000
25.6600000000
27.2600000000
27.8800000000
25.1600000000
26.6700000000
28.460

In [37]:
import sqlite3

# Create a SQL connection to our SQLite database
con = sqlite3.connect("NEO.db")

cur = con.cursor()

# The result of a "cursor.execute" can be iterated over by row
for row in cur.execute('SELECT v_rel FROM NEOs;'):
    print(row)

# Be sure to close the connection
con.close()

(11.9842220841328,)
(11.1602139720087,)
(45.8448630366018,)
(28.1882829187049,)
(6.88443029643995,)
(9.95877021760284,)
(11.4430529093987,)
(7.04444043149188,)
(7.89056849079978,)
(10.6566230480628,)
(7.2292378449434,)
(7.53471398911999,)
(20.9967349687611,)
(14.261911981888,)
(4.1088479045737,)
(14.0833111553654,)
(9.77217223997576,)
(0.650036704947336,)
(8.83164298110677,)
(19.6104473678073,)
(7.15829856261938,)
(12.8183926828615,)
(11.9171649687952,)
(7.53204634099846,)
(14.699735591818,)
(6.44671576142614,)
(7.26569264045889,)
(2.7820922481087,)
(16.7327480648458,)
(5.95497975203764,)
(6.37967766581341,)
(17.2116654145002,)
(25.1971608646488,)
(11.3767202424355,)
(10.584442249383,)
(11.2419964727166,)
(11.6029565022567,)
(11.7619658293727,)
(5.65179413914172,)
(7.93846708077749,)
(7.69889252688939,)
(8.9026295720249,)
(6.10862002104616,)
(8.07544764860904,)
(16.6552167009845,)
(8.09387140284267,)
(14.3263800601051,)
(9.17488028923707,)
(12.7604553991961,)
(5.92936807363732,)
(13.65

In [43]:
con = sqlite3.connect("NEO.db")
cursor = con.cursor()

cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
print(cursor.fetchall())

[('NEOs',)]


In [ ]:
# Lunar Distance  384400 km (~.002570 au)

In [35]:
# Chart 2 - Bubble Chart - Closeness to Earth and Threat bubble
# API request can be replaced with a df filter of 'dist-max=0.05', maybe a sort then select range
basic_url_2 = 'https://ssd-api.jpl.nasa.gov/cad.api?date-min=2022-01-01&date-max=2072-01-01&dist-max=0.02'
response2 = requests.get(basic_url_2)
data_2 = response2.json() 

# might need to tighten up range, .02 max reduced resutls to 1538

In [ ]:
# Chart 3 - Large Table - All data retreived with filters

# Currently would be a ~11 by ~5000 list
# Could filter overlapping objects from chart 1 and chart 2 results
# Could possible add inner planets, need to clarify what NEO body output means

# filtering by inner planets upgrade option(**bonus**)

